In [2]:
import pandas as pd
from bs4 import BeautifulSoup
import requests
import re
import csv
import time
import os
import numpy as np
import concurrent.futures
import random

In [3]:
df = pd.read_csv('initial_test_companies_url.csv', header=None)
df.columns = ['URL', 'Category']

#### Remove duplicate values

In [4]:
df.drop_duplicates(subset='URL', keep=False, inplace=True)
df = df.reset_index(drop=True)

In [5]:
elements = len(df)
n = 2
while elements%n != 0:
    elements -=1

split_step = int(elements/n)
split_from = 0
split_to = split_step
links = []
for i in range(n-1):
    links.append(df.iloc[split_from:split_to,0])
    split_from = split_to
    split_to = split_to + split_step
    
links.append(df.iloc[split_from:,0])


#### Data Scraping

In [6]:
file_name = 'company_data.csv'
data_row = {}

fieldnames = ['Company Name', 'Registration code', 'VAT', 
            'Manager', 'Address', 'Website', 'Work hours', 
            'SS insurer code', 'Transport', 'Authorized capital', 
            'Company age', 'Employees', 'Average salary', 
            'Social insurance taxes', 'Sales revenue From', 
            'Sales revenue To', 'Rating', 'No. Rated', 'Category',
            'Other Categories', 'Facebook']

In [7]:
data_row.keys()

dict_keys([])

In [8]:
def getProxyList(v=True):
    """Scrapes and return a list of available free proxies"""
    URL = 'https://free-proxy-list.net/'
    html = requests.get(URL, timeout=3)
    soup = BeautifulSoup(html.content, 'lxml')

    # Find the first tbody tag and retrieve al tr with data td stored in list
    table = soup.find('tbody')
    rows = [row.find_all('td') for row in table.find_all('tr')]


    # Append a proxy adress to the list if anonimity is 'elite proxy'
    proxy_list = []
    for row in rows:
        if row[4].text == 'elite proxy' and row[6].text == 'yes':
            proxy_list.append(row[0].text + ':' + row[1].text)
    if v == True:
        print(f'{len(proxy_list)} Have been found.')
    return proxy_list

In [9]:
def loadPage(URL, delay, headers, v=True):
    """Requests a URL with with random header and available proxy"""
    proxy_list = getProxyList()
    random.shuffle(proxy_list)
    
    header = {'User-Agent': random.choice(headers)}
    
    for proxy in proxy_list: 
        try:
            if v == True:
                print('Trying proxy: {}'.format(proxy))
            r = requests.get(URL, proxies={'https': proxy}, headers=header, timeout=5)
            break
        except:
            if v == True:
                print('{} is not valid proxy.'.format(proxy))
            continue
    if v == True:
        print(f'Succes! Using proxy: {proxy}')   
    soup = BeautifulSoup(r.content, 'lxml')
    time.sleep(delay)
    return (soup, proxy)

In [10]:
def unusuaTrafficCheck(soup):
    """Checks for capcha"""
    result = soup.find('div',{'class':'content unusualTraffic'})
    return bool(result)

In [11]:
def getHeaderName(ind, table_rows):
    return table_rows[ind].find_all('td')[1].get_text()

def getTableData(ind, table_rows):
    return table_rows[ind].find_all('td')[2].get_text().strip()

In [12]:
def parseTableData(soup):
    """Parse company data table"""

    table_rows = soup.find('table').find_all('tr')
    
    # Data headers of intrest
    data_filter = ['Registration code', 'VAT', 'Manager', 'Address',
                  'Website', 'Work hours', 'SS insurer code',
                  'Average salary', 'Social insurance taxes',
                  'Transport', 'Authorized capital', 'Company age', 'Facebook']

    for row in table_rows:
        header_name = getHeaderName(table_rows.index(row), table_rows)
        table_data = getTableData(table_rows.index(row), table_rows)
        if header_name in data_filter:
            data_row[header_name] = table_data
        elif header_name == 'Employees':
            data_row[header_name] = table_data.split(' ')[0]
        elif header_name == 'Sales revenue':
            result = re.search(r'\d+\s*\d*\s*[-]\s*\d*\s*\d*', table_data)
            data_row[header_name + ' From'] = result[0].replace(' ', '').split('-')[0]
            data_row[header_name + ' To'] = result[0].replace(' ', '').split('-')[1]
        elif header_name == 'Rating':
            try:
                rating = table_rows[table_rows.index(row)].find_all('td')[2].select('span')[0].get_text()
                no_rated = table_rows[table_rows.index(row)].find_all('td')[2].select('span')[2].get_text()
                data_row[header_name] = rating
                data_row['No. Rated'] = no_rated
            except IndexError:
                continue

In [13]:
def getCompanyName(soup):
    """Adds Company Name to the data row"""
    data_row['Company Name'] = soup.select('.fn')[0].get_text()

def parseCategories(soup):
    # Get main category and subcategories
    try:
        category = soup.find('div', {'class':'floatLeft about'}).find_all('a')
    except AttributeError:
        category = soup.find('div', {'class':'about floatLeft'}).find_all('a')
    else:
        data_row['Category'] = category[0]['title']
        # Run this part only if there is more than 1 category.
        other_categories = [i['title'] for i in category if len(category)>1]
        data_row['Other Categories'] = other_categories

In [14]:
def writeHeaders(file_name, fieldnames):
    with open(file_name, 'w', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
        writer.writeheader()

def writeDataRow(file_name, data_row, fieldnames):
    with open(file_name, 'a', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
        writer.writerow(data_row)

In [16]:
def loadUserAgents(filename):
    '''Loads User-Agents from csv file'''
    with open(filename, 'r', newline='') as f:
        reader = csv.reader(f)
        user_agents = []
        for row in reader:
            user_agents.append(row[0])
    return user_agents

user_agents = loadUserAgents('user_agents.csv')

def scrape(links):
    for i in links: 
        start = time.perf_counter()
        soup, proxy = loadPage(i, 1, user_agents)

        if unusuaTrafficCheck(soup):
            print('Capcha detected!')

        getCompanyName(soup)
        parseTableData(soup)
        parseCategories(soup)
        writeDataRow(file_name, data_row, fieldnames)
        finish = time.perf_counter()
        print(f'Succesfully scraped URL: {i}')
        print(f'Scraping took: {finish-start}')

In [86]:
writeHeaders(file_name, fieldnames)
with concurrent.futures.ThreadPoolExecutor() as executor:
    task1 = executor.submit(scrape, links[0])
    task2 = executor.submit(scrape, links[1])

        


52 Have been found.
Trying proxy: 43.245.218.217:25
52 Have been found.
Trying proxy: 103.111.225.17:8080
43.245.218.217:25 is not valid proxy.
Trying proxy: 103.240.77.98:30093
103.111.225.17:8080 is not valid proxy.
Trying proxy: 139.59.60.174:8080
139.59.60.174:8080 is not valid proxy.
Trying proxy: 103.110.104.2:8080
103.110.104.2:8080 is not valid proxy.
Trying proxy: 193.239.86.249:3128
193.239.86.249:3128 is not valid proxy.
Trying proxy: 37.120.239.150:3128
37.120.239.150:3128 is not valid proxy.
Trying proxy: 157.230.103.189:36366
103.240.77.98:30093 is not valid proxy.
Trying proxy: 167.71.239.213:8080
157.230.103.189:36366 is not valid proxy.
Trying proxy: 51.254.237.77:3129
Succes! Using proxy: 167.71.239.213:8080
51.254.237.77:3129 is not valid proxy.
Trying proxy: 51.222.173.56:3128
51.222.173.56:3128 is not valid proxy.
Trying proxy: 185.128.136.231:3128
Succes! Using proxy: 185.128.136.231:3128


In [17]:
for i in links[0]:
    print(i)

https://rekvizitai.vz.lt/en/company/bestela/
https://rekvizitai.vz.lt/en/company/dekvota/
https://rekvizitai.vz.lt/en/company/findir_consulting/
https://rekvizitai.vz.lt/en/company/uab_gisera/
https://rekvizitai.vz.lt/en/company/uab_spinoza/
https://rekvizitai.vz.lt/en/company/visi_apskaitos_sprendimai/
https://rekvizitai.vz.lt/en/company/acl/
https://rekvizitai.vz.lt/en/company/margrupe/
https://rekvizitai.vz.lt/en/company/konjura/
https://rekvizitai.vz.lt/en/company/offerens/
https://rekvizitai.vz.lt/en/company/euromanai/
https://rekvizitai.vz.lt/en/company/kodralita/
https://rekvizitai.vz.lt/en/company/apskaita_ir_finansai/
https://rekvizitai.vz.lt/en/company/dvigubas_irasas_apskaita/
https://rekvizitai.vz.lt/en/company/imfina/
https://rekvizitai.vz.lt/en/company/integre/
https://rekvizitai.vz.lt/en/company/verslolita/
https://rekvizitai.vz.lt/en/company/finotika/
https://rekvizitai.vz.lt/en/company/profinas/
https://rekvizitai.vz.lt/en/company/apskaitos_ir_verslo_sprendimu_biuras/


https://rekvizitai.vz.lt/en/company/bendra_lietuvos_ir_vokietijos_imone_uab_dukatas/
https://rekvizitai.vz.lt/en/company/e_luneckienes_imone_vingrija/
https://rekvizitai.vz.lt/en/company/elena_140263825/
https://rekvizitai.vz.lt/en/company/elvyros_sakalauskienes_ii/
https://rekvizitai.vz.lt/en/company/fortransas/
https://rekvizitai.vz.lt/en/company/gailutes_belickienes_imone/
https://rekvizitai.vz.lt/en/company/geri_tikslai/
https://rekvizitai.vz.lt/en/company/gimtasis_sodzius/
https://rekvizitai.vz.lt/en/company/i_blakunovos_ii/
https://rekvizitai.vz.lt/en/company/i_sapranauskienes_ii/
https://rekvizitai.vz.lt/en/company/j_burzinskienes_imone_adisenda/
https://rekvizitai.vz.lt/en/company/jono_matuseviciaus_imone/
https://rekvizitai.vz.lt/en/company/jurates_markovienes_ii/
https://rekvizitai.vz.lt/en/company/karmazinai/
https://rekvizitai.vz.lt/en/company/kazimieros_stonienes_ii/
https://rekvizitai.vz.lt/en/company/kriaukle/
https://rekvizitai.vz.lt/en/company/lietuvos_ir_panamos_uab_l

https://rekvizitai.vz.lt/en/company/naujasis_idejos_kelias/
https://rekvizitai.vz.lt/en/company/netylancios_stygos/
https://rekvizitai.vz.lt/en/company/new_active_systems/
https://rekvizitai.vz.lt/en/company/nuolaidu_katalogai/
https://rekvizitai.vz.lt/en/company/nvestus/
https://rekvizitai.vz.lt/en/company/oberinas/
https://rekvizitai.vz.lt/en/company/olorenta/
https://rekvizitai.vz.lt/en/company/omneda/
https://rekvizitai.vz.lt/en/company/on_ads/
https://rekvizitai.vz.lt/en/company/optimali_raidos_estetika/
https://rekvizitai.vz.lt/en/company/oscar_capital/
https://rekvizitai.vz.lt/en/company/pastele/
https://rekvizitai.vz.lt/en/company/patranka/
https://rekvizitai.vz.lt/en/company/uab_pca_marketing_group/
https://rekvizitai.vz.lt/en/company/piketo_reklama/
https://rekvizitai.vz.lt/en/company/uab_pinigu_masina/
https://rekvizitai.vz.lt/en/company/politines_komunikacijos_asociacija/
https://rekvizitai.vz.lt/en/company/precizi/
https://rekvizitai.vz.lt/en/company/uab_press_lt/
https://

https://rekvizitai.vz.lt/en/company/zemes_ukio_kooperatyvas_aukstaitijos_aruodai/
https://rekvizitai.vz.lt/en/company/bikunai/
https://rekvizitai.vz.lt/en/company/zemes_ukio_kb_bio_leua/
https://rekvizitai.vz.lt/en/company/cm_kaunas/
https://rekvizitai.vz.lt/en/company/compactas/
https://rekvizitai.vz.lt/en/company/daisiva/
https://rekvizitai.vz.lt/en/company/danora/
https://rekvizitai.vz.lt/en/company/zemes_ukio_kooperatyvas_danukis/
https://rekvizitai.vz.lt/en/company/zemes_ukio_kooperatyvas_dubysa_agro/
https://rekvizitai.vz.lt/en/company/zemes_ukio_kooperatyvas_dusetu_krasto_gaspadoriai/
https://rekvizitai.vz.lt/en/company/dzukijos_servisas/
https://rekvizitai.vz.lt/en/company/edo_ukis/
https://rekvizitai.vz.lt/en/company/unimerchants_baltic/
https://rekvizitai.vz.lt/en/company/ekoangus/
https://rekvizitai.vz.lt/en/company/ekoaruodai/
https://rekvizitai.vz.lt/en/company/ekolaukai/
https://rekvizitai.vz.lt/en/company/ekox/
https://rekvizitai.vz.lt/en/company/engineringa/
https://rek

https://rekvizitai.vz.lt/en/company/ramdaile/
https://rekvizitai.vz.lt/en/company/vsi_ramybes_galerija/
https://rekvizitai.vz.lt/en/company/remeliu_dizainas_i_yankouskaya_ii/
https://rekvizitai.vz.lt/en/company/uab_scenos_darbai/
https://rekvizitai.vz.lt/en/company/studija_michael_mccready/
https://rekvizitai.vz.lt/en/company/siauliu_rajono_savivaldybes_kulturos_centras/
https://rekvizitai.vz.lt/en/company/v_miskinio_imone/
https://rekvizitai.vz.lt/en/company/arasai/
https://rekvizitai.vz.lt/en/company/aromus/
https://rekvizitai.vz.lt/en/company/coconas/
https://rekvizitai.vz.lt/en/company/dmo_music_group/
https://rekvizitai.vz.lt/en/company/dokumedija/
https://rekvizitai.vz.lt/en/company/dvidesimt_trys/
https://rekvizitai.vz.lt/en/company/ii_focus_studio/
https://rekvizitai.vz.lt/en/company/galerija_rotunda_v_daugio_privati_firma/
https://rekvizitai.vz.lt/en/company/g_staskausko_skulpturos_ir_keramikos_studija/
https://rekvizitai.vz.lt/en/company/gedimino_zilinsko_meno_centras/
https:

...

https://rekvizitai.vz.lt/en/company/uab_nova_energia/
https://rekvizitai.vz.lt/en/company/novus_agro/
https://rekvizitai.vz.lt/en/company/uab_novus_energy/
https://rekvizitai.vz.lt/en/company/obwalden/
https://rekvizitai.vz.lt/en/company/olmena/
https://rekvizitai.vz.lt/en/company/palektra/
https://rekvizitai.vz.lt/en/company/uab_pamario_jegaines/
https://rekvizitai.vz.lt/en/company/parfelija/
https://rekvizitai.vz.lt/en/company/pavilniu_saules_slenis_25/
https://rekvizitai.vz.lt/en/company/pavilniu_saules_slenis_4/
https://rekvizitai.vz.lt/en/company/pavilniu_saules_slenis_5/
https://rekvizitai.vz.lt/en/company/pavilniu_saules_slenis_6/
https://rekvizitai.vz.lt/en/company/saules_saltinis/
https://rekvizitai.vz.lt/en/company/pietu_saules_slenis/
https://rekvizitai.vz.lt/en/company/pietuskiu_elektra/
https://rekvizitai.vz.lt/en/company/pietuskiu_saules_jegaine/
https://rekvizitai.vz.lt/en/company/e_gadisausko_imone/
https://rekvizitai.vz.lt/en/company/suvalkijos_bio_energija/
https://re

https://rekvizitai.vz.lt/en/company/s_o_renginiai/
https://rekvizitai.vz.lt/en/company/smagus/
https://rekvizitai.vz.lt/en/company/aktyvistas/
https://rekvizitai.vz.lt/en/company/duo_opus/
https://rekvizitai.vz.lt/en/company/vinetu_kaimas/
https://rekvizitai.vz.lt/en/company/anvus/
https://rekvizitai.vz.lt/en/company/dziaugsmo_slenis/
https://rekvizitai.vz.lt/en/company/istruk/
https://rekvizitai.vz.lt/en/company/mano_disco/
https://rekvizitai.vz.lt/en/company/vejo_tunelis/
https://rekvizitai.vz.lt/en/company/muses_salto/
https://rekvizitai.vz.lt/en/company/pajurio_kartingai/
https://rekvizitai.vz.lt/en/company/virtualus_kiemas/
https://rekvizitai.vz.lt/en/company/aktyvus_laisvalaikis/
https://rekvizitai.vz.lt/en/company/arbatos_akademija/
https://rekvizitai.vz.lt/en/company/sandena/
https://rekvizitai.vz.lt/en/company/vailit/
https://rekvizitai.vz.lt/en/company/10_biciuliu/
https://rekvizitai.vz.lt/en/company/abosera/
https://rekvizitai.vz.lt/en/company/basa_blusa/
https://rekvizitai.

https://rekvizitai.vz.lt/en/company/jaukumo_laikas/
https://rekvizitai.vz.lt/en/company/jaunimo_centras_veikama/
https://rekvizitai.vz.lt/en/company/karve_ant_ledo/
https://rekvizitai.vz.lt/en/company/kerbas_lt/
https://rekvizitai.vz.lt/en/company/lietuviu_etnines_kulturos_draugija/
https://rekvizitai.vz.lt/en/company/meno_dalis/
https://rekvizitai.vz.lt/en/company/neformaliojo_svietimo_debatu_centras/
https://rekvizitai.vz.lt/en/company/penkios_dukros/
https://rekvizitai.vz.lt/en/company/raseiniu_r_kulturos_centras/
https://rekvizitai.vz.lt/en/company/remigijaus_akcija/
https://rekvizitai.vz.lt/en/company/renginiu_asistentai/
https://rekvizitai.vz.lt/en/company/renginiu_fotografavimas/
https://rekvizitai.vz.lt/en/company/renginiu_laboratorija/
https://rekvizitai.vz.lt/en/company/rexus/
https://rekvizitai.vz.lt/en/company/uab_saules_parkas/
https://rekvizitai.vz.lt/en/company/camerata_klaipeda/
https://rekvizitai.vz.lt/en/company/viesoji_istaiga_pajurio_dudos/
https://rekvizitai.vz.lt/

https://rekvizitai.vz.lt/en/company/bourgeois_boheme_fintech/
https://rekvizitai.vz.lt/en/company/clearshift/
https://rekvizitai.vz.lt/en/company/invl_baltic_farmland/
https://rekvizitai.vz.lt/en/company/dipocket/
https://rekvizitai.vz.lt/en/company/domestique_asset_management/
https://rekvizitai.vz.lt/en/company/vanepay/
https://rekvizitai.vz.lt/en/company/e_finansai_lt/
https://rekvizitai.vz.lt/en/company/esbs_finansavimo_sistemos/
https://rekvizitai.vz.lt/en/company/uab_euro_hes/
https://rekvizitai.vz.lt/en/company/fa_finansai/
https://rekvizitai.vz.lt/en/company/finansai_jums/
https://rekvizitai.vz.lt/en/company/finansu_balansas/
https://rekvizitai.vz.lt/en/company/finansu_paslaugos/
https://rekvizitai.vz.lt/en/company/finansu_sistemos/
https://rekvizitai.vz.lt/en/company/finansu_verslas/
https://rekvizitai.vz.lt/en/company/flywire_europe/
https://rekvizitai.vz.lt/en/company/busto_mokejimai/
https://rekvizitai.vz.lt/en/company/fondegama/
https://rekvizitai.vz.lt/en/company/plusplus

https://rekvizitai.vz.lt/en/company/medziotoju_klubas_sasna/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_senasis_vilkas/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_studentas/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_sungailiskis/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_svedasai/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_satrija/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_saulys_kaunas/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_siaurinis/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_sunskai/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_tauras/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_trakai/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_truskava/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_varene/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_vasaknos/
https://rekvizitai.vz.lt/en/company/medziotoju_klubas_vidsodis/
https://rekvizitai.vz.lt/en/compan

In [85]:
i = ['https://rekvizitai.vz.lt/en/company/kingsbury_baltic_properties/']
scrape(i)

57 Have been found.
Trying proxy: 185.128.136.231:3128
Succes! Using proxy: 185.128.136.231:3128
Succesfully scraped URL: https://rekvizitai.vz.lt/en/company/kingsbury_baltic_properties/
Scraping took: 10.65609647097881 seconds using proxy: 185.128.136.231:3128


In [77]:
print(soup)

NameError: name 'soup' is not defined

type(links[0])